# Capstone Project - The Battle of the Neighborhoods (Week 2)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)



## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a restaurant. Specifically, this report will be targeted to stakeholders interested in opening an **Chinese restaurant** in **Copnehagen**, Denmark.

Since there are lots of restaurants in City of Copenhagen we will try to detect **locations that are not already crowded with restaurants**. We are also particularly interested in **areas with no Chinese restaurants in vicinity**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing restaurants in the neighborhood (any type of restaurant)
* number of and distance to Chinese restaurants in the neighborhood, if any
* distance of neighborhood from city center

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **Google Maps API reverse geocoding**
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of copenhagen center will be obtained using **Google Maps API geocoding** of well known Copnehagen location (Tivoli)

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 12x12 killometers centered around CPH city center.

Let's first find the latitude & longitude of Berlin city center, using specific, well known address and Google Maps geocoding API.

In [1]:
import requests

#api_key removed for private reason


def get_coordinates(api_key, address, verbose=False):
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&address={}'.format(api_key, address)
        response = requests.get(url).json()
        results = response['results']
        geographical_data = results[0]['geometry']['location'] # get geographical coordinates
        lat = geographical_data['lat']
        lon = geographical_data['lng']
        return [lat, lon]
    
address = 'Tivoli, Copenhagen, Denmark'
cph_center = get_coordinates(api_key, address)
print('Coordinate of {}: {}'.format(address, cph_center))

Coordinate of Tivoli, Copenhagen, Denmark: [55.6736841, 12.5681471]


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~6km from **Tivoli**. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [2]:
#!pip install shapely
import shapely.geometry

#!pip install pyproj
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Copenhagen center longitude={}, latitude={}'.format(cph_center[1], cph_center[0]))
x, y = lonlat_to_xy(cph_center[1], cph_center[0])
print('Copenhage center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Copenhage center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Copenhagen center longitude=12.5681471, latitude=55.6736841


c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':


Copenhage center UTM X=347071.89878700825, Y=6172443.342626065
Copenhage center longitude=12.5681471, latitude=55.6736841


c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [3]:
cph_center_x, cph_center_y = lonlat_to_xy(cph_center[1], cph_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = cph_center_x - 6000
x_step = 600
y_min = cph_center_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(cph_center_x, cph_center_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pypr

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

...

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

364 candidate neighborhood centers generated.


c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [4]:
#!pip install folium

import folium

In [5]:
map_copenhagen = folium.Map(location=cph_center, zoom_start=13)
folium.Marker(cph_center, popup='Tivoli').add_to(map_copenhagen)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_berlin) 
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_copenhagen)
    #folium.Marker([lat, lon]).add_to(map_berlin)
map_copenhagen

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~6km from Tivoli. 

Let's now use Google Maps API to get approximate addresses of those locations.

In [6]:
def get_address(api_key, latitude, longitude, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&latlng={},{}'.format(api_key, latitude, longitude)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        address = results[0]['formatted_address']
        return address
    except:
        return None

addr = get_address(api_key, cph_center[0], cph_center[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(cph_center[0], cph_center[1], addr))

Reverse geocoding check
-----------------------
Address of [55.6736841, 12.5681471] is: Vesterbrogade 3, 1630 København, Denmark


In [7]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(api_key, lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', Denmark', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [9]:
addresses[0:10]

['Sneppestien, 2770 Kastrup',
 'Unnamed Road, 2770 Kastrup',
 'Kanonvej, 2770 Kastrup',
 'Richard Mortensens Vej 20, 2300 København S',
 'Hf. Kongedybet 31, 2770 Kastrup',
 'Hf. Sydgrænsen 98, 2770 Kastrup',
 'Præstefælledvej 32, 2770 Kastrup',
 'Selinevej 10, 2300 København',
 'Selinevej 8, 2300 København',
 'Fasanskovvej, 2770 Kastrup']

Looking good. Let's now place all this into a Pandas dataframe.

In [10]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address   Latitude  Longitude  \
0                    Sneppestien, 2770 Kastrup  55.621803  12.542770   
1                   Unnamed Road, 2770 Kastrup  55.621993  12.552289   
2                       Kanonvej, 2770 Kastrup  55.622183  12.561808   
3  Richard Mortensens Vej 20, 2300 København S  55.622372  12.571327   
4              Hf. Kongedybet 31, 2770 Kastrup  55.622560  12.580846   
5              Hf. Sydgrænsen 98, 2770 Kastrup  55.622747  12.590365   
6             Præstefælledvej 32, 2770 Kastrup  55.622934  12.599884   
7                 Selinevej 10, 2300 København  55.626180  12.528198   
8                  Selinevej 8, 2300 København  55.626372  12.537718   
9                   Fasanskovvej, 2770 Kastrup  55.626563  12.547238   

               X             Y  Distance from center  
0  345271.898787  6.166728e+06           5992.495307  
1  345871.898787  6.166728e+06           5840.376700  
2  346471.898787  6.166728e+06           5747.173218  
3  347071.898787  6.166728e+06           5715.767665  
4  347671.898787  6.166728e+06           5747.173218  
5  348271.898787  6.166728e+06           5840.376700  
6  348871.898787  6.166728e+06           5992.495307  
7  344371.898787  6.167247e+06           5855.766389  
8  344971.898787  6.167247e+06           5604.462508  
9  345571.898787  6.167247e+06           5408.326913

...and let's now save/persist this data into local file.

In [11]:
df_locations.to_pickle('./locations.pkl')    

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on restaurants in neighborhoods.

We're interested in venues in 'food' category, but only those that are proper restaurants - coffe shops, pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in out list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific 'Chinese restaurant' category, as we need info on Chinese restaurants in the neighborhood.

Foursquare credentials are defined in hidden cell bellow.

In [15]:
# foursquare client id and secret removed for private reason


12.593589826548099

In [66]:
# Category IDs corresponding to Chinese restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

chinese_restaurant_category = ['4bf58dd8d48988d145941735','52af3a5e3cf9994f4e043bea','52af3a723cf9994f4e043bec','52af3a7c3cf9994f4e043bed',
                               '58daa1558bbb0b01f18ec1d3','52af3a673cf9994f4e043beb','52af3a903cf9994f4e043bee','4bf58dd8d48988d1f5931735',
                               '52af3a9f3cf9994f4e043bef','52af3aaa3cf9994f4e043bf0','52af3ab53cf9994f4e043bf1','52af3abe3cf9994f4e043bf2',
                               '52af3ac83cf9994f4e043bf3','52af3ad23cf9994f4e043bf4','52af3add3cf9994f4e043bf5','52af3af23cf9994f4e043bf7',
                               '52af3ae63cf9994f4e043bf6','52af3afc3cf9994f4e043bf8','52af3b053cf9994f4e043bf9','52af3b213cf9994f4e043bfa',
                               '52af3b293cf9994f4e043bfb','52af3b343cf9994f4e043bfc','52af3b3b3cf9994f4e043bfd','52af3b463cf9994f4e043bfe',
                               '52af3b633cf9994f4e043c01','52af3b513cf9994f4e043bff','52af3b593cf9994f4e043c00','52af3b6e3cf9994f4e043c02',
                               '52af3b773cf9994f4e043c03','52af3b813cf9994f4e043c04','52af3b913cf9994f4e043c06','52af3b9a3cf9994f4e043c07',
                               '52af3ba23cf9994f4e043c08','4bf58dd8d48988d142941735']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Danmark', '')
    address = address.replace(', Denmark', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius, limit):
    version = '20210504'
    radius=350
    limit=100
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, food_category, radius, limit)
    results = requests.get(url).json()['response']['groups'][0]['items']
    venues = [(item['venue']['id'],
               item['venue']['name'],
               get_categories(item['venue']['categories']),
               (item['venue']['location']['lat'], item['venue']['location']['lng']),
               format_address(item['venue']['location']),
               item['venue']['location']['distance']) for item in results]
    return venues

In [77]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found chinese restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    chinese_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, client_id, client_secret, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_chinese = is_restaurant(venue_categories, specific_filter=chinese_restaurant_category)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_chinese, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_chinese:
                    chinese_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, chinese_restaurants, location_restaurants

restaurants, chinese_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    

Obtaining venues around candidate locations: . . . .

c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':


 . . . . . . . .

c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See

 . . .

...

 . . . .

c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':


 .

c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See

 . . done.


In [79]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of Chinese restaurants:', len(chinese_restaurants))
print('Percentage of Chinese restaurants: {:.2f}%'.format(len(chinese_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 910
Total number of Chinese restaurants: 57
Percentage of Chinese restaurants: 6.26%
Average number of restaurants in neighborhood: 2.2115384615384617


In [80]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('50ee96cde4b0e87d58f8f8ca', 'Metroselskabets buffet', 55.62123981569403, 12.57720028407603, 'Metrovej 5', 272, False, 347437.27584053134, 6166588.740428939)
('4bf2c9f320960f47d9a76e2f', 'STORM Restaurant', 55.62685184043494, 12.57684792034416, 'Ørestads Boulevard, 2300 København S', 72, False, 347436.89927264286, 6167213.877572173)
('4d0a42c186b0236a7066b806', 'Bøfhus', 55.63000417665359, 12.577926352804022, 'Arne Jacobsens Allé 12 (Ørestads Boulevard), 2300 København S', 256, False, 347517.02770176064, 6167562.218639369)
('569929aa498e9c75520a74fe', 'Dalle Valle', 55.62980320872566, 12.578587715246742, 'Arne Jacobsens Allé 12 (Ørestads Boulevard), 2300 København S', 255, False, 347557.87474741193, 6167538.406884203)
('4b631ba5f964a52092632ae3', 'The American Restaurant & Diner', 55.62998395877257, 12.57802083776939, 'Arne Jacobsens Allé 12 (Ørestads Boulevard), 2300 Købehavn S', 254, False, 347522.89624124067, 6167559.761679759)
('578e7

In [83]:
print('List of Chinese restaurants')
print('---------------------------')
for r in list(chinese_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(chinese_restaurants))

List of Chinese restaurants
---------------------------
('4c7bd8983badb1f7d0085654', 'Sushi Bar', 55.63016969862762, 12.57829171679973, "Arne Jacobsens Allé 12 (i Field's), 2300 København S", 228, True, 347540.6672647109, 6167579.830873596)
('4b8818f2f964a52093df31e3', 'Den kinesiske mur', 55.64544184709592, 12.615031446657293, 'Sundbyvester plads, København', 188, True, 349911.5570402637, 6169198.833563842)
('583092ae03cf2531661c9eef', 'Asian Palace', 55.652683, 12.52057, 'Carl Jacobsens Vej 17K, 2500 Valby', 271, True, 343997.12530958024, 6170212.840016224)
('4cbb44bbbac93704e902f17c', 'Power Grill', 55.654739, 12.60331665, 'Englandsvej 35, 2300 Copenhagen S', 112, True, 349210.23160897265, 6170258.599578909)
('4b96594bf964a5206ec734e3', 'Den Lykkelige Familie', 55.655697366830275, 12.604196611206135, 'Englandsvej 32, 2300 København', 97, True, 349269.26683094003, 6170363.310870565)
('4b797fdef964a520f6fc2ee3', 'Wan Hao', 55.65436355737855, 12.610527941821353, 'Amagerbrogade 160, 230

In [84]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: Sjælør Kebab, Sjælørs Kebab & Burger House, Sag Kantine
Restaurants around location 102: Den Sorte Gryde, Sydhavnen
Restaurants around location 103: Meadow Garden Restaurant
Restaurants around location 104: 
Restaurants around location 105: Scarpetta, Cofoco Le Marché
Restaurants around location 106: 
Restaurants around location 107: 
Restaurants around location 108: 
Restaurants around location 109: stegogbras.dk, Power Grill, Den Lykkelige Familie
Restaurants around location 110: Il Gambero Rosso, Gnam Gnam, Bone's, Wan Hao, Sumo Sushi, Thai House, Southern Grill


Let's now see all the collected restaurants in our area of interest on map, and let's also show Chinese restaurants in different color.

In [91]:
map_copenhagen = folium.Map(location=cph_center, zoom_start=13)
folium.Marker(cph_center, popup='Tivoli').add_to(map_copenhagen)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_chinese = res[6]
    color = 'red' if is_chinese else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_copenhagen)
map_copenhagen

Looking good. So now we have all the restaurants in area within few kilometers from **Tivoli** -- city center, and we know which ones are Chinese restaurants! We also know which restaurants exactly are in vicinity of neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Italian restaurant!

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Copenhagen that have low restaurant density, particularly those with low number of Chinese restaurants. We will limit our analysis to area ~6km around city center.

In first step we have collected the required **data: location and type (category) of every restaurant within 6km from Copenhagen center** (Tivoli). We have also **identified Chinese restaurants** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of '**restaurant density**' across different areas of Copenhagen - we will use **heatmaps** to identify a few promising areas close to center with low number of restaurants in general (*and* no Italian restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 250 meters**, and we want locations **without Chinese restaurants in radius of 400 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of restaurants in area candidate**:

In [92]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 2.2115384615384617


Address   Latitude  Longitude  \
0                    Sneppestien, 2770 Kastrup  55.621803  12.542770   
1                   Unnamed Road, 2770 Kastrup  55.621993  12.552289   
2                       Kanonvej, 2770 Kastrup  55.622183  12.561808   
3  Richard Mortensens Vej 20, 2300 København S  55.622372  12.571327   
4              Hf. Kongedybet 31, 2770 Kastrup  55.622560  12.580846   
5              Hf. Sydgrænsen 98, 2770 Kastrup  55.622747  12.590365   
6             Præstefælledvej 32, 2770 Kastrup  55.622934  12.599884   
7                 Selinevej 10, 2300 København  55.626180  12.528198   
8                  Selinevej 8, 2300 København  55.626372  12.537718   
9                   Fasanskovvej, 2770 Kastrup  55.626563  12.547238   

               X             Y  Distance from center  Restaurants in area  \
0  345271.898787  6.166728e+06           5992.495307                    0   
1  345871.898787  6.166728e+06           5840.376700                    0   
2  346471.898787  6.166728e+06           5747.173218                    0   
3  347071.898787  6.166728e+06           5715.767665                    0   
4  347671.898787  6.166728e+06           5747.173218                    1   
5  348271.898787  6.166728e+06           5840.376700                    0   
6  348871.898787  6.166728e+06           5992.495307                    0   
7  344371.898787  6.167247e+06           5855.766389                    0   
8  344971.898787  6.167247e+06           5604.462508                    0   
9  345571.898787  6.167247e+06           5408.326913                    0   

   Distance to Chinese restaurant  
0                           10000  
1                           10000  
2                           10000  
3                           10000  
4                           10000  
5                           10000  
6                           10000  
7                           10000  
8                           10000  
9                           10000

OK, now let's calculate the **distance to nearest Chinese restaurant from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [93]:
distances_to_chinese_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in chinese_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_chinese_restaurant.append(min_distance)

df_locations['Distance to Chinese restaurant'] = distances_to_chinese_restaurant

In [94]:
df_locations.head(10)

Address   Latitude  Longitude  \
0                    Sneppestien, 2770 Kastrup  55.621803  12.542770   
1                   Unnamed Road, 2770 Kastrup  55.621993  12.552289   
2                       Kanonvej, 2770 Kastrup  55.622183  12.561808   
3  Richard Mortensens Vej 20, 2300 København S  55.622372  12.571327   
4              Hf. Kongedybet 31, 2770 Kastrup  55.622560  12.580846   
5              Hf. Sydgrænsen 98, 2770 Kastrup  55.622747  12.590365   
6             Præstefælledvej 32, 2770 Kastrup  55.622934  12.599884   
7                 Selinevej 10, 2300 København  55.626180  12.528198   
8                  Selinevej 8, 2300 København  55.626372  12.537718   
9                   Fasanskovvej, 2770 Kastrup  55.626563  12.547238   

               X             Y  Distance from center  Restaurants in area  \
0  345271.898787  6.166728e+06           5992.495307                    0   
1  345871.898787  6.166728e+06           5840.376700                    0   
2  346471.898787  6.166728e+06           5747.173218                    0   
3  347071.898787  6.166728e+06           5715.767665                    0   
4  347671.898787  6.166728e+06           5747.173218                    1   
5  348271.898787  6.166728e+06           5840.376700                    0   
6  348871.898787  6.166728e+06           5992.495307                    0   
7  344371.898787  6.167247e+06           5855.766389                    0   
8  344971.898787  6.167247e+06           5604.462508                    0   
9  345571.898787  6.167247e+06           5408.326913                    0   

   Distance to Chinese restaurant  
0                     2423.561542  
1                     1873.800516  
2                     1366.969714  
3                      972.668508  
4                      862.300326  
5                     1122.960231  
6                     1580.669955  
7                     2989.236353  
8                     2590.216460  
9                     1996.672015

In [95]:
print('Average distance to closest Chinese restaurant from each area center:', df_locations['Distance to Chinese restaurant'].mean())

Average distance to closest Chinese restaurant from each area center: 1086.217846090107


OK, so **on average Chinese restaurant can be found within ~1100m** from every area center candidate. That's fairly close, so we need to filter our areas carefully

Let's crete a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show a few circles indicating distance of 1km, 2km and 3km from Tivoli.

In [96]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

chinese_latlons = [[res[2], res[3]] for res in chinese_restaurants.values()]

In [97]:
from folium import plugins
from folium.plugins import HeatMap

map_copenhagen = folium.Map(location=cph_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_copenhagen) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_copenhagen)
folium.Marker(cph_center).add_to(map_copenhagen)
folium.Circle(cph_center, radius=1000, fill=False, color='white').add_to(map_copenhagen)
folium.Circle(cph_center, radius=2000, fill=False, color='white').add_to(map_copenhagen)
folium.Circle(cph_center, radius=3000, fill=False, color='white').add_to(map_copenhagen)
map_copenhagen

Looks like a few pockets of low restaurant density closest to city center can be found **south, south-west from Tivoli**. 

Let's create another heatmap map showing **heatmap/density of Chinese restaurants** only.

In [98]:
map_copenhagen = folium.Map(location=cph_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_copenhagen) #cartodbpositron cartodbdark_matter
HeatMap(chinese_latlons).add_to(map_copenhagen)
folium.Marker(cph_center).add_to(map_copenhagen)
folium.Circle(cph_center, radius=1000, fill=False, color='white').add_to(map_copenhagen)
folium.Circle(cph_center, radius=2000, fill=False, color='white').add_to(map_copenhagen)
folium.Circle(cph_center, radius=3000, fill=False, color='white').add_to(map_copenhagen)
map_copenhagen

This map is not so 'hot' (Chinese restaurants represent a subset of ~6% of all restaurants in Copenhagen) but it also indicates higher density of existing Chinese restaurants directly north and west from Tivoli, with closest pockets of **low Chinese restaurant density positioned south-west and north-east from city center**.

Based on this we will now focus our analysis on areas *south-west, north-east from Copenhagen center* - we will move the center of our area of interest and reduce it's size to have a radius of **2.5km**. This places our location candidates mostly in boroughs **København S and Amager** (another potentially interesting borough is **valby** with large low restaurant density west from city center, however this borough is less interesting to stakeholders as it's mostly residental and less popular with tourists).

### København SV and Amager

Analysis of popular travel guides and web sites often mention København SV and Amager as beautifull, interesting, rich with culture, 'hip' and 'cool' Copenhagen neighborhoods popular with tourists and loved by københavner.

Popular with tourists, alternative and bohemian but booming and trendy, relatively close to city center and well connected, those boroughs appear to justify further analysis.

Let's define new, more narrow region of interest, which will include low-restaurant-count parts of København SV and Amager closest to Tivoli.

In [99]:
roi_x_min = cph_center_x - 2000
roi_y_max = cph_center_y + 1000
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_berlin = folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_copenhagen)
folium.Marker(cph_center).add_to(map_copenhagen)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_copenhagen)
map_copenhagen

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


Not bad - this nicely covers all the pockets of low restaurant density in København S and Østerport closest to Copenhagen center.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

In [100]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

...

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

2261 candidate neighborhood centers generated.


c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


OK. Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest Chinese restaurant**.

In [101]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_chinese_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, chinese_restaurants)
    roi_chinese_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [102]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Chinese restaurant':roi_chinese_distances})

df_roi_locations.head(10)

Latitude  Longitude              X             Y  Restaurants nearby  \
0  55.637916  12.577515  347521.898787  6.168443e+06                   3   
1  55.637947  12.579103  347621.898787  6.168443e+06                   3   
2  55.638521  12.568738  346971.898787  6.168530e+06                   0   
3  55.638552  12.570325  347071.898787  6.168530e+06                   0   
4  55.638584  12.571912  347171.898787  6.168530e+06                   0   
5  55.638615  12.573499  347271.898787  6.168530e+06                   0   
6  55.638646  12.575087  347371.898787  6.168530e+06                   3   
7  55.638678  12.576674  347471.898787  6.168530e+06                   3   
8  55.638709  12.578261  347571.898787  6.168530e+06                   3   
9  55.638740  12.579848  347671.898787  6.168530e+06                   3   

   Distance to Chinese restaurant  
0                      863.715695  
1                      867.324107  
2                     1107.345814  
3                     1059.462626  
4                     1019.169937  
5                      987.397420  
6                      964.987030  
7                      952.599744  
8                      950.627465  
9                      959.134444

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 250 meters**, and **no Chinese restaurants in radius of 400 meters**.

In [103]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_chi_distance = np.array(df_roi_locations['Distance to Chinese restaurant']>=400)
print('Locations with no Chinese restaurants within 400m:', good_chi_distance.sum())

good_locations = np.logical_and(good_res_count, good_chi_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than two restaurants nearby: 1427
Locations with no Chinese restaurants within 400m: 1513
Locations with both conditions met: 1250


Let's see how this looks on a map.

In [104]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_berlin = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_copenhagen)
HeatMap(restaurant_latlons).add_to(map_copenhagen)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_copenhagen)
folium.Marker(cph_center).add_to(map_copenhagen)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_copenhagen) 
map_copenhagen

Looking good. We now have a bunch of locations fairly close to Tivoli (mostly in København SV , Østerport , Amager, valby and south-west corner of København kommunen), and we know that each of those locations has no more than two restaurants in radius of 250m, and no Chinese restaurant closer than 400m. Any of those locations is a potential candidate for a new Chinese restaurant, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [105]:
map_copenhagen = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_copenhagen)
folium.Marker(cph_center).add_to(map_copenhagen)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_berlin)
map_copenhagen

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Chinese restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [106]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_berlin = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_copenhagen)
HeatMap(restaurant_latlons).add_to(map_berlin)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_copenhagen)
folium.Marker(cph_center).add_to(map_copenhagen)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_copenhagen) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_copenhagen)
map_copenhagen

c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\python37\lib\site-packages\ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
c:\py

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [107]:
map_copenhagen = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(cph_center).add_to(map_copenhagen)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_copenhagen)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_copenhagen)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_copenhagen) 
map_copenhagen

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [108]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(api_key, lat, lon).replace(', Denmark', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, cph_center_x, cph_center_y)
    print('{}{} => {:.1f}km from Tivoli'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis



c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':


Otto Busses Vej 43, 2450 København                 => 2.3km from Tivoli


c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':


Stjernevej 5, 2300 København                       => 3.7km from Tivoli


...

Nordre Digevej 52, 2300 København                  => 2.8km from Tivoli


c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':


Grundejerforeningen Havnestads Havnepark - åbent alle dage kl. 7.00-22.00, Islands Brygge 22, 2300 København S => 0.9km from Tivoli


c:\python37\lib\site-packages\ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':


Sundbyvestervej 50, 2300 København                 => 3.5km from Tivoli


This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no Chinese restaurants nearby, all zones being fairly close to city center (all less than 4km from Tivoli, and about half of those less than 2km from Tivoli). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. Most of the zones are located in københavn S(2450) and Amager(2300) boroughs, which we have identified as interesting due to being popular with tourists, fairly close to city center and well connected by public transport.

In [117]:
map_copenhagen = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(cph_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_copenhagen)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_copenhagen) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_copenhagen)
map_copenhagen

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of restaurants in Copenhagen (~910 in our initial area of interest which was 12x12km around Tivoli), there are pockets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected north and west from Tivoli, so we focused our attention to areas south and south-west, corresponding to boroughs København SV, Amager and north-west corner of København. Another borough was identified as potentially interesting (valby and Bornbyst), but our attention was focused on København SV and Amager which offer a combination of popularity among tourists, closeness to city center, strong socio-economic dynamics *and* a number of pockets of low restaurant density.

After directing our attention to this more narrow area of interest (covering approx. 5x5km south-east from tIVOLI) we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with an Italian restaurant closer than 400m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Chinese restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Copenhagen center but not crowded with existing restaurants (particularly Chinese) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Copenhagen areas close to center with low number of restaurants (particularly Chinese restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Chinese restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general boroughs that justify further analysis (København SV and Amager), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.